In [1]:
import numpy as np
import pandas as pd
import requests
from bs4 import BeautifulSoup
import urllib.request
from urllib.request import urlopen
import json

import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans

In [2]:
url = 'https://en.wikipedia.org/wiki/Special_wards_of_Tokyo#List_of_special_wards'

html = urlopen(url)

soup = BeautifulSoup(html,'html.parser')


In [3]:
soup.title.string

'Special wards of Tokyo - Wikipedia'

In [4]:
right_table=soup.find('table',{"class":'wikitable sortable'})

In [5]:
tokyo_ward_table = pd.DataFrame(columns =['No.', 'Flag', 'Special Ward Name', 'Kanji', 'Population (as of October 2016)', 'Density (km2)', 'Area (km2)', 'Major Districts'])

tokyo_ward_table

for row in right_table.findAll("tr"):
    rows = []
    for cell in row.find_all('td'):
        rows.append(cell.text.lstrip('0').replace('\n',''))
        
    if len(rows) == 8:
        tokyo_ward_table.loc[len(tokyo_ward_table)] = rows
        
tokyo_ward_table.dtypes

No.                                object
Flag                               object
Special Ward Name                  object
Kanji                              object
Population (as of October 2016)    object
Density (km2)                      object
Area (km2)                         object
Major Districts                    object
dtype: object

In [6]:
tokyo_ward_table = tokyo_ward_table[['Special Ward Name', 'Population (as of October 2016)', 'Area (km2)']] 

tokyo_ward_table

Special Ward Name Population (as of October 2016) Area (km2)
0            Chiyoda                          59,441      11.66
1               Chūō                         147,620      10.21
2             Minato                         248,071      20.37
3           Shinjuku                         339,211      18.22
4             Bunkyō                         223,389      11.29
5              Taitō                         200,486      10.11
6             Sumida                         260,358      13.77
7               Kōtō                         502,579      40.16
8          Shinagawa                         392,492      22.84
9             Meguro                         280,283      14.67
10            OtaŌta                         722,608      60.66
11          Setagaya                         910,868      58.05
12           Shibuya                         227,850      15.11
13            Nakano                         332,902      15.59
14          Suginami                         570,483      34.06
15           Toshima                         294,673      13.01
16              Kita                         345,063      20.61
17           Arakawa                         213,648      10.16
18          Itabashi                         569,225      32.22
19            Nerima                         726,748      48.08
20            Adachi                         674,067      53.25
21        Katsushika                         447,140      34.80
22           Edogawa                         685,899      49.90

In [7]:
pip install geopy

Note: you may need to restart the kernel to use updated packages.


In [8]:
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent='tokyo_locations')

long_lat_df = tokyo_ward_table['Special Ward Name'].apply(geolocator.geocode).apply(lambda x: (x.latitude, x.longitude))


tokyo_ward_table[['Latitude', 'Longitude']] = long_lat_df.apply(pd.Series)

tokyo_ward_table

Special Ward Name Population (as of October 2016) Area (km2)   Latitude  \
0            Chiyoda                          59,441      11.66  35.693810   
1               Chūō                         147,620      10.21  35.666255   
2             Minato                         248,071      20.37  35.643227   
3           Shinjuku                         339,211      18.22  35.693763   
4             Bunkyō                         223,389      11.29  35.718810   
5              Taitō                         200,486      10.11  35.717450   
6             Sumida                         260,358      13.77  35.700429   
7               Kōtō                         502,579      40.16  35.649154   
8          Shinagawa                         392,492      22.84  35.599252   
9             Meguro                         280,283      14.67  35.621250   
10            OtaŌta                         722,608      60.66 -36.968498   
11          Setagaya                         910,868      58.05  35.646096   
12           Shibuya                         227,850      15.11  35.664596   
13            Nakano                         332,902      15.59  35.718123   
14          Suginami                         570,483      34.06  35.699493   
15           Toshima                         294,673      13.01  35.736156   
16              Kita                         345,063      20.61  -0.220164   
17           Arakawa                         213,648      10.16  35.737529   
18          Itabashi                         569,225      32.22  35.774143   
19            Nerima                         726,748      48.08  35.748360   
20            Adachi                         674,067      53.25  35.783703   
21        Katsushika                         447,140      34.80  35.751733   
22           Edogawa                         685,899      49.90  35.678278   

     Longitude  
0   139.753216  
1   139.775565  
2   139.740055  
3   139.703632  
4   139.744732  
5   139.790859  
6   139.805017  
7   139.812790  
8   139.738910  
9   139.688014  
10  174.940847  
11  139.656270  
12  139.698711  
13  139.664468  
14  139.636288  
15  139.714222  
16  -78.512327  
17  139.781310  
18  139.681209  
19  139.638735  
20  139.795319  
21  139.863816  
22  139.871091

In [9]:
Lat_list = tokyo_ward_table['Latitude'].tolist()
Long_list = tokyo_ward_table['Longitude'].tolist()
print ("Old Latitude List: ", Lat_list)
print ("Old Longitude List: ", Long_list)

replace_latitudes = {-0.2201641:35.7652805, -36.9684982:35.5671615}
replace_longitudes = {-78.5123274:139.6949053, 174.9408469:139.6693728}

latitudes_new = [replace_latitudes.get(n3,n3) for n3 in Lat_list]
longitudes_new = [replace_longitudes.get(n4,n4) for n4 in Long_list]

print("New Latitude List: ",latitudes_new)
print("New Longitude List: ",longitudes_new)

##Replacing incorrect Geopy locations with correct ones (based on Google maps)

Old Latitude List:  [35.6938097, 35.666255, 35.6432274, 35.6937632, 35.71881, 35.71745, 35.700429, 35.649154, 35.599252, 35.62125, -36.9684982, 35.646096, 35.6645956, 35.718123, 35.6994929, 35.736156, -0.2201641, 35.737529, 35.774143, 35.74836, 35.783703, 35.751733, 35.678278]
Old Longitude List:  [139.7532163, 139.775565, 139.7400553, 139.7036319, 139.744732, 139.790859, 139.805017, 139.81279, 139.73891, 139.688014, 174.9408469, 139.65627, 139.6987107, 139.664468, 139.6362876, 139.714222, -78.5123274, 139.78131, 139.681209, 139.638735, 139.795319, 139.863816, 139.871091]
New Latitude List:  [35.6938097, 35.666255, 35.6432274, 35.6937632, 35.71881, 35.71745, 35.700429, 35.649154, 35.599252, 35.62125, 35.5671615, 35.646096, 35.6645956, 35.718123, 35.6994929, 35.736156, 35.7652805, 35.737529, 35.774143, 35.74836, 35.783703, 35.751733, 35.678278]
New Longitude List:  [139.7532163, 139.775565, 139.7400553, 139.7036319, 139.744732, 139.790859, 139.805017, 139.81279, 139.73891, 139.688014, 1

In [10]:
tokyo_ward_table['Latitude'] = latitudes_new
tokyo_ward_table['Longitude'] = longitudes_new

tokyo_ward_table

Special Ward Name Population (as of October 2016) Area (km2)   Latitude  \
0            Chiyoda                          59,441      11.66  35.693810   
1               Chūō                         147,620      10.21  35.666255   
2             Minato                         248,071      20.37  35.643227   
3           Shinjuku                         339,211      18.22  35.693763   
4             Bunkyō                         223,389      11.29  35.718810   
5              Taitō                         200,486      10.11  35.717450   
6             Sumida                         260,358      13.77  35.700429   
7               Kōtō                         502,579      40.16  35.649154   
8          Shinagawa                         392,492      22.84  35.599252   
9             Meguro                         280,283      14.67  35.621250   
10            OtaŌta                         722,608      60.66  35.567161   
11          Setagaya                         910,868      58.05  35.646096   
12           Shibuya                         227,850      15.11  35.664596   
13            Nakano                         332,902      15.59  35.718123   
14          Suginami                         570,483      34.06  35.699493   
15           Toshima                         294,673      13.01  35.736156   
16              Kita                         345,063      20.61  35.765281   
17           Arakawa                         213,648      10.16  35.737529   
18          Itabashi                         569,225      32.22  35.774143   
19            Nerima                         726,748      48.08  35.748360   
20            Adachi                         674,067      53.25  35.783703   
21        Katsushika                         447,140      34.80  35.751733   
22           Edogawa                         685,899      49.90  35.678278   

     Longitude  
0   139.753216  
1   139.775565  
2   139.740055  
3   139.703632  
4   139.744732  
5   139.790859  
6   139.805017  
7   139.812790  
8   139.738910  
9   139.688014  
10  139.669373  
11  139.656270  
12  139.698711  
13  139.664468  
14  139.636288  
15  139.714222  
16  139.694905  
17  139.781310  
18  139.681209  
19  139.638735  
20  139.795319  
21  139.863816  
22  139.871091

In [11]:
## Foursquare API

Client_ID = 'PK2XLPBZPKZWNWIZRFAMDII4M2SQSA0OC4KQVHMVTE1WMK01'
Client_Secret = 'WLPBOMBHUWIHXH05TP2BGA3XCWGBGKQV1GH13ICJ4SMLHHS2'
Access_Token = 'RNQKBXER512ZKTZM0SD0QCXVY4U2ZSFEUFXS5BWTJYW4XTGW'
Version = 20201226

print('My credentials:')
print('My CLIENT_ID: ' + Client_ID)
print('My CLIENT_SECRET:' + Client_Secret)


My credentials:
My CLIENT_ID: PK2XLPBZPKZWNWIZRFAMDII4M2SQSA0OC4KQVHMVTE1WMK01
My CLIENT_SECRET:WLPBOMBHUWIHXH05TP2BGA3XCWGBGKQV1GH13ICJ4SMLHHS2


In [12]:
!pip install folium

import folium
from pandas.io.json import json_normalize
from IPython.display import Image 
from IPython.core.display import HTML 


     |████████████████████████████████| 93 kB 2.6 MB/s  eta 0:00:01


In [13]:
## Getting the latitude and longitude of Tokyo, Japan

address = 'Tokyo, Japan'

geolocator = Nominatim(user_agent="tokyo_locations")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print(latitude, longitude)

35.6828387 139.7594549


In [14]:
##Special Wards in Map Form

ward_map = folium.Map(location = [latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(tokyo_ward_table['Latitude'], tokyo_ward_table['Longitude'], tokyo_ward_table['Special Ward Name']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html = True)
    folium.CircleMarker(
        [lat, lng],
        radius = 13,
        popup = label,
        color = 'Red',
        fill = True,
        fill_color = '#3186cc',
        fill_opacity = 0.7,
        parse_html = False).add_to(ward_map)  
    
ward_map


In [15]:
##Searching ramen shops in Tokyo
radius = 50000  ## 50 KM from city center
LIMIT = 500   ## Limit 500 Ramen Restaurants
search_query = 'Ramen'

url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&oauth_token={}&v={}&query={}&radius={}&limit={}'.format(
    Client_ID, 
    Client_Secret, 
    latitude, 
    longitude, 
    Access_Token,
    Version,
    search_query,
    radius, 
    LIMIT)

results = requests.get(url).json()

In [16]:
ramen = results['response']['venues']

ramen_df = pd.json_normalize(ramen)

ramen_df

id  \
0   5f28f4bd33646a5aea649bce   
1   5f07261e874dc91be658d2de   
2   5af02d5c0d2be7002c5870d9   
3   5947c00b1fa7633e49c2e1c5   
4   55507da7498ebfd16d1f66cd   
5   571bd57d498ea3998018aa6f   
6   506d0b84582f6852a966a036   
7   4b5a9531f964a52078cc28e3   
8   5a280bc0e185f34584befc75   
9   55c4041e498e70491192cc6b   
10  5ca189fec824ae002c5cd230   
11  5f559d2f0b69a228a162ad90   
12  4bb06abef964a520af443ce3   
13  5c7b91ab54b7a90025cbe071   
14  563a0190cd10c59dc00c2320   
15  5a98d664c365886e7affe17e   
16  543e5ec3498ee8034fd6a5a6   
17  5735a5fc498e902957562782   
18  5a2a30f97269fe0585e84c5c   
19  4b70d419f964a5207b302de3   
20  5dbfc03f68a0e10007132519   
21  5bd257e0cad1b60039471e28   
22  5ce6387906fb60002cebedbf   
23  5ae566feca18ea002c69a375   
24  4b6aa4c6f964a52070da2be3   
25  5bbc9d03e1f228002cfdc650   
26  5587f099498e08017047c031   
27  5fcce2607077392d1eeb9a5e   
28  4b7a0802f964a520da1f2fe3   
29  513ec6b3e4b05b7b6cd6833b   
30  4e94f64602d5bf622948568a   
31  4b59614cf964a520968628e3   
32  4c22fc3e13c00f47196888de   
33  4fc2e8a4e4b069481ef1be71   
34  5e6ca5c2227ee800085f9e9c   
35  598d1fc15c68384be55dfac7   
36  58521c968ae36373ba2a1169   
37  4d9d2d0c79d1ba7ac0fd3388   
38  5cb5e446f709c1002c7163cf   
39  53da163a498e6b4679a2be25   
40  5c19b83c286fda002c2f148e   
41  51a03b82498e45602bcfc7f0   
42  549fa8fe498e58bd4f820856   
43  4e58678dd22d61e8f3492755   
44  4c273930f1272d7ff8d687c5   
45  4b722255f964a52055702de3   
46  509b3e92e4b08e75e64ac211   
47  56b9ad5e498e903b98f27985   
48  56156563498e4ac2de63fa6c   
49  5f8e6ada85875f56eb677cfa   

                                                 name  \
0                            Nippon Ramen 凛 RIN Tokyo   
1                                        RAMEN AVENUE   
2                         RAMEN 火影 produced by 麺処 ほん田   
3                                 Ramen ドゥエ Edo Japan   
4                                       RAMEN TOMIRAI   
5          Homemade Ramen Muginae (Homemade Ramen 麦苗)   
6                        Ramen 1/20 (Ramen にじゅうぶんのいち)   
7             Shin-Yokohama Ramen Museum (新横浜ラーメン博物館)   
8                          Ramen Jiro (ラーメン二郎 神田神保町店)   
9                                      RAMENバル shogun   
10                                    Ramen House 東福舎   
11                        RAMEN EXPRESS 博多一風堂 東京ソラマチ店   
12                   Tokyo Ramen Street (東京ラーメンストリート)   
13                          Ramen Gekisenku (ラーメン激戦区)   
14                                       RAMEN GOSSOU   
15                               UNDERGROUND RAMEN 頑者   
16                               UNDERGROUND RAMEN 頑者   
17                         ramen shigetomi (らーめんシゲトミ)   
18                           RAMEN FACTORY. TORISETSU   
19                           Ramen Misozen (らーめん みそ膳)   
20  Ippudo Ramen Express (IPPUDO RAMEN EXPRESS テラス...   
21                                Ramen Gyoku (らーめん玉)   
22                           Ramen Moritaro (ラーメン盛太郎)   
23                                 Kinton Ramen Tokyo   
24       Karashibi Miso Ramen Kikanbo (カラシビ味噌らー麺 鬼金棒)   
25                                   YUJI Ramen Tokyo   
26                           Ramen Moritaro (ラーメン盛太郎)   
27                          Ramen Kagemusha (らーめん影武者)   
28                               Akanoren (博多麺房 赤のれん)   
29                                       RAMEN GOTTSU   
30                             Ramen Bario (らーめん バリ男)   
31                     Kanda Ramen Waizu (神田ラーメン わいず)   
32                             Ramen Bario (らーめん バリ男)   
33                 Hakata Ramen Yoshimaru (博多らーめん 由丸)   
34                                  下北澤Ramen KUWAJIMA   
35                    Ramen Takahashi (焼きあご塩らー麺 たかはし)   
36                              Ramen Ichiro (らーめん一郎)   
37                               T's Tantan (T'sたんたん)   
38                            Ramen Butayama (ラーメン豚山)   
39                             Ramen Kimaru (らーめん 喜丸)   
40             Ramen Lemon & Fromage (らぁ麺 レモン&フロマージュ)   

In [17]:
filtered_columns = ['name', 'categories'] + [col for col in ramen_df.columns if col.startswith('location.')]+['id']
ramen_df_filtered = ramen_df.loc[:, filtered_columns]

def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']
    
ramen_df_filtered['categories'] = ramen_df_filtered.apply(get_category_type, axis=1)

ramen_df_filtered.columns = [column.split('.')[-1] for column in ramen_df_filtered.columns]

ramen_df_filtered

name  \
0                            Nippon Ramen 凛 RIN Tokyo   
1                                        RAMEN AVENUE   
2                         RAMEN 火影 produced by 麺処 ほん田   
3                                 Ramen ドゥエ Edo Japan   
4                                       RAMEN TOMIRAI   
5          Homemade Ramen Muginae (Homemade Ramen 麦苗)   
6                        Ramen 1/20 (Ramen にじゅうぶんのいち)   
7             Shin-Yokohama Ramen Museum (新横浜ラーメン博物館)   
8                          Ramen Jiro (ラーメン二郎 神田神保町店)   
9                                      RAMENバル shogun   
10                                    Ramen House 東福舎   
11                        RAMEN EXPRESS 博多一風堂 東京ソラマチ店   
12                   Tokyo Ramen Street (東京ラーメンストリート)   
13                          Ramen Gekisenku (ラーメン激戦区)   
14                                       RAMEN GOSSOU   
15                               UNDERGROUND RAMEN 頑者   
16                               UNDERGROUND RAMEN 頑者   
17                         ramen shigetomi (らーめんシゲトミ)   
18                           RAMEN FACTORY. TORISETSU   
19                           Ramen Misozen (らーめん みそ膳)   
20  Ippudo Ramen Express (IPPUDO RAMEN EXPRESS テラス...   
21                                Ramen Gyoku (らーめん玉)   
22                           Ramen Moritaro (ラーメン盛太郎)   
23                                 Kinton Ramen Tokyo   
24       Karashibi Miso Ramen Kikanbo (カラシビ味噌らー麺 鬼金棒)   
25                                   YUJI Ramen Tokyo   
26                           Ramen Moritaro (ラーメン盛太郎)   
27                          Ramen Kagemusha (らーめん影武者)   
28                               Akanoren (博多麺房 赤のれん)   
29                                       RAMEN GOTTSU   
30                             Ramen Bario (らーめん バリ男)   
31                     Kanda Ramen Waizu (神田ラーメン わいず)   
32                             Ramen Bario (らーめん バリ男)   
33                 Hakata Ramen Yoshimaru (博多らーめん 由丸)   
34                                  下北澤Ramen KUWAJIMA   
35                    Ramen Takahashi (焼きあご塩らー麺 たかはし)   
36                              Ramen Ichiro (らーめん一郎)   
37                               T's Tantan (T'sたんたん)   
38                            Ramen Butayama (ラーメン豚山)   
39                             Ramen Kimaru (らーめん 喜丸)   
40             Ramen Lemon & Fromage (らぁ麺 レモン&フロマージュ)   
41                         Ramen Horiuchi (らぁめん ほりうち)   
42                               IPPUDO RAMEN EXPRESS   
43                   Ramen Keisuke Tori King (鶏王けいすけ)   
44                         Shinamen Hashigo (支那麺 はしご)   
45                           Ramen Jiro (ラーメン二郎 三田本店)   
46                Kitakata Ramen Ban Nai (喜多方ラーメン 坂内)   
47                               Ramen Ninja (らーめん忍者)   
48                 Hakata Ramen Yoshimaru (博多らーめん 由丸)   
49          Homemade Ramen Aomugi (Homemade Ramen 青麦)   

                       categories        address                crossStreet  \
0                Ramen Restaurant       丸の内1-9-1                    グランスタ東京   
1                      Food Court         内幸町1-7                   日比谷グルメゾン   
2                Ramen Restaurant        大井1-1-9                        NaN   
3                Ramen Restaurant       内幸町2-1-6             日比谷パークフロント B1F   
4                Ramen Restaurant      代々木1-33-2                        NaN   
5                Ramen Restaurant     南大井6-11-10                        NaN   
6                Ramen Restaurant      東尾久2-19-9                    西脇ビル 1F   
7                      Theme Park  港北区新横浜2-14-21                        NaN   
8                Ramen Restaurant    神田神保町1-21-4                        NaN   
9                Ramen Restaurant       銀座7-3-13           ニューギンザ1号館 B1F-1F   
10               Ramen Restaurant            NaN                        NaN   
11               Ramen Restaurant        押上1-1-2                        NaN   
12                     Food Court       丸の内1-9-1                 東京駅一番街 B1F   
13                     Food Court  

In [18]:
##Ramen Data Visualizations

ramen_map = folium.Map(location=[latitude, longitude], zoom_start=12)

for lat, lng, label in zip(ramen_df_filtered.lat, ramen_df_filtered.lng, ramen_df_filtered.categories):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.5
    ).add_to(ramen_map)
    
for lat, lng, neighborhood in zip(tokyo_ward_table['Latitude'], tokyo_ward_table['Longitude'], tokyo_ward_table['Special Ward Name']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html = True)
    folium.CircleMarker(
        [lat, lng],
        radius = 13,
        popup = label,
        color = 'Red',
        fill = True,
        fill_color = '#3186cc',
        fill_opacity = 0.7,
        parse_html = False).add_to(ramen_map)
    
ramen_map

##Seems the Chiyoda and Chuo wards have the most ramen shops (makes sense as they are essentially the city center)

In [19]:
## Venues Visualizations - let's explore more of Chiyoda

Chiyoda_lat = 35.693810
Chiyoda_long = 139.753216

radius = 1000 ## 1 KM around Chiyoda

url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}'.format(Client_ID, Client_Secret, Chiyoda_lat, Chiyoda_long, Version, radius)
url

'https://api.foursquare.com/v2/venues/explore?client_id=PK2XLPBZPKZWNWIZRFAMDII4M2SQSA0OC4KQVHMVTE1WMK01&client_secret=WLPBOMBHUWIHXH05TP2BGA3XCWGBGKQV1GH13ICJ4SMLHHS2&ll=35.69381,139.753216&v=20201226&radius=1000'

In [20]:
results = requests.get(url).json()
items = results['response']['groups'][0]['items']
items[0]

{'reasons': {'count': 0,
  'items': [{'summary': 'This spot is popular',
    'type': 'general',
    'reasonName': 'globalInteractionReason'}]},
 'venue': {'id': '4b5ab0ddf964a520f5d028e3',
  'name': 'Nippon Budokan (日本武道館)',
  'location': {'address': '北の丸公園2-3',
   'lat': 35.69335624055126,
   'lng': 139.74986493587494,
   'labeledLatLngs': [{'label': 'display',
     'lat': 35.69335624055126,
     'lng': 139.74986493587494}],
   'distance': 307,
   'postalCode': '102-8321',
   'cc': 'JP',
   'city': '東京',
   'state': '東京都',
   'country': '日本',
   'formattedAddress': ['北の丸公園2-3', '千代田区, 東京都', '102-8321', '日本']},
  'categories': [{'id': '4bf58dd8d48988d184941735',
    'name': 'Stadium',
    'pluralName': 'Stadiums',
    'shortName': 'Stadium',
    'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/arts_entertainment/stadium_',
     'suffix': '.png'},
    'primary': True}],
  'photos': {'count': 0, 'groups': []}},
 'referralId': 'e-0-4b5ab0ddf964a520f5d028e3-0'}

In [21]:
chiyoda_df = pd.json_normalize(items) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories'] + [col for col in chiyoda_df.columns if col.startswith('venue.location.')] + ['venue.id']
chiyoda_df_filtered = chiyoda_df.loc[:, filtered_columns]

# filter the category for each row
chiyoda_df_filtered['venue.categories'] = chiyoda_df_filtered.apply(get_category_type, axis=1)

# clean columns
chiyoda_df_filtered.columns = [col.split('.')[-1] for col in chiyoda_df_filtered.columns]

chiyoda_df_filtered.head(10)

name                 categories  \
0                     Nippon Budokan (日本武道館)                    Stadium   
1                    Kitanomaru Park (北の丸公園)                       Park   
2                   Jimbocho Kurosu (神保町 黒須)           Ramen Restaurant   
3                     Kanda Tendonya (神田天丼家)         Tempura Restaurant   
4  National Museum of Modern Art (東京国立近代美術館)                 Art Museum   
5                         Bondy (欧風カレー ボンディ)  Japanese Curry Restaurant   
6                Mori no Butchers (森のブッチャーズ)                  Gastropub   
7                         Warayakiya (わらやき屋)                   Sake Bar   
8                      Shimizumon Gate (清水門)              Historic Site   
9      Jimbocho Shokuniku Center (神保町食肉センター)                  BBQ Joint   

       address        lat         lng  \
0     北の丸公園2-3  35.693356  139.749865   
1     北の丸公園1-1  35.691653  139.751201   
2  神田神保町3-1-19  35.695539  139.754851   
3  神田神保町3-1-14  35.695765  139.754682   
4     北の丸公園3-1  35.690541  139.754694   
5     神田神保町2-3  35.695544  139.757356   
6     一ツ橋2-6-5  35.694770  139.755980   
7     九段北1-3-5  35.696017  139.751388   
8        北の丸公園  35.692685  139.752681   
9    神田神保町2-16  35.697206  139.757284   

                                      labeledLatLngs  distance postalCode  cc  \
0  [{'label': 'display', 'lat': 35.69335624055126...       307   102-8321  JP   
1  [{'label': 'display', 'lat': 35.69165274543888...       301   102-0091  JP   
2  [{'label': 'display', 'lat': 35.69553894340011...       242   101-0051  JP   
3  [{'label': 'display', 'lat': 35.69576473597737...       254   101-0051  JP   
4  [{'label': 'display', 'lat': 35.69054128670216...       387   102-8322  JP   
5  [{'label': 'display', 'lat': 35.695544, 'lng':...       421   101-0051  JP   
6  [{'label': 'display', 'lat': 35.69477, 'lng': ...       271   101-0003  JP   
7  [{'label': 'display', 'lat': 35.696017, 'lng':...       296   105-0022  JP   
8  [{'label': 'display', 'lat': 35.69268530308536...       134   102-0091  JP   
9  [{'label': 'display', 'lat': 35.697206, 'lng':...       527   101-0051  JP   

   city state country                                   formattedAddress  \
0    東京   東京都      日本                [北の丸公園2-3, 千代田区, 東京都, 102-8321, 日本]   
1    東京   東京都      日本                [北の丸公園1-1, 千代田区, 東京都, 102-0091, 日本]   
2  千代田区   東京都      日本             [神田神保町3-1-19, 千代田区, 東京都, 101-0051, 日本]   
3  千代田区   東京都      日本             [神田神保町3-1-14, 千代田区, 東京都, 101-0051, 日本]   
4    東京   東京都      日本                [北の丸公園3-1, 千代田区, 東京都, 102-8322, 日本]   
5    東京   東京都      日本  [神田神保町2-3 (神田古書センタービル 2F), 千代田区, 東京都, 101-0051...   
6  千代田区   東京都      日本                [一ツ橋2-6-5, 千代田区, 東京都, 101-0003, 日本]   
7    東京   東京都      日本  [九段北1-3-5 (九段第2清新ビル 1F-2F), 千代田区, 東京都, 105-002...   
8    東京   東京都      日本                   [北の丸公園, 千代田区, 東京都, 102-0091, 日本]   
9    東京   東京都      日本               [神田神保町2-16, 千代田区, 東京都, 101-0051, 日本]   

  neighborhood     crossStreet                        id  
0          NaN             NaN  4b5ab0ddf964a520f5d028e3  
1          NaN             NaN  4b7237fdf964a52064742de3  
2          NaN             NaN  581680a638fa2b62abcb3196  
3          NaN             NaN  4eb750bf469073bbc6f5d659  
4        Kōkyo             NaN  4b5be55ff964a520281c29e3  
5          NaN   神田古書センタービル 2F  4c37fdd13849c9286cd7beb1  
6          NaN             NaN  532ace8c498ef90c9a5b3b35  
7          NaN  九段第2清新ビル 1F-2F  547ef228498ef8757b174f96  
8          NaN             NaN  4b79404ff964a520d2f02ee3  
9          NaN             NaN  4c3a9587be4620a1a9210b13

In [28]:
chiyoda_df_filtered['categories'].value_counts()

Café                         6
Japanese Curry Restaurant    3
Ramen Restaurant             3
Sushi Restaurant             2
BBQ Joint                    2
Historic Site                2
Trail                        1
Bed & Breakfast              1
Comedy Club                  1
Coffee Shop                  1
Beer Bar                     1
Park                         1
Bookstore                    1
Art Museum                   1
Sake Bar                     1
Gastropub                    1
Tempura Restaurant           1
Stadium                      1
Name: categories, dtype: int64

In [22]:
chiyoda_map = folium.Map(location=[Chiyoda_lat, Chiyoda_long], zoom_start=15)

for lat, lng, label in zip(chiyoda_df_filtered.lat, chiyoda_df_filtered.lng, chiyoda_df_filtered.categories):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='purple',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.5
    ).add_to(chiyoda_map)
    
chiyoda_map

In [23]:
## Venues across Tokyo

def getNearbyVenues(names, latitudes, longitudes, radius=50000, LIMIT=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            Client_ID, 
            Client_Secret, 
            Version, 
            latitude, 
            longitude, 
            radius,
            LIMIT
        )
            
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venues_list in venues_list for item in venues_list])
    nearby_venues.columns = ['Special Ward', 
                  'Latitude', 
                  'Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [24]:
Tokyo_Ward_Venues = getNearbyVenues(names=tokyo_ward_table['Special Ward Name'],
                                   latitudes=tokyo_ward_table['Latitude'],
                                   longitudes=tokyo_ward_table['Longitude']
                                   )

Tokyo_Ward_Venues

Chiyoda
Chūō
Minato
Shinjuku
Bunkyō
Taitō
Sumida
Kōtō
Shinagawa
Meguro
OtaŌta
Setagaya
Shibuya
Nakano
Suginami
Toshima
Kita
Arakawa
Itabashi
Nerima
Adachi
Katsushika
Edogawa


Special Ward   Latitude   Longitude                           Venue  \
0         Chiyoda  35.693810  139.753216   KITTE Garden (屋上庭園 KITTEガーデン)   
1         Chiyoda  35.693810  139.753216              Aman Tokyo (アマン東京)   
2         Chiyoda  35.693810  139.753216                  Tsujihan (つじ半)   
3         Chiyoda  35.693810  139.753216                     Maruka (丸香)   
4         Chiyoda  35.693810  139.753216  Rice Curry Manten (ライスカレーまんてん)   
...           ...        ...         ...                             ...   
2295      Edogawa  35.678278  139.871091                Morimoto (焼鳥 森本)   
2296      Edogawa  35.678278  139.871091   Park Hyatt Tokyo (パークハイアット東京)   
2297      Edogawa  35.678278  139.871091         Aigre Douce (エーグル ドゥース)   
2298      Edogawa  35.678278  139.871091                    Fuglen Tokyo   
2299      Edogawa  35.678278  139.871091                 365 Days (365日)   

      Venue Latitude  Venue Longitude             Venue Category  
0          35.679654       139.765169                  Roof Deck  
1          35.685236       139.765401                      Hotel  
2          35.680763       139.771563         Donburi Restaurant  
3          35.696693       139.760121            Udon Restaurant  
4          35.698213       139.757428  Japanese Curry Restaurant  
...              ...              ...                        ...  
2295       35.658501       139.698633        Yakitori Restaurant  
2296       35.685575       139.690639                      Hotel  
2297       35.722327       139.700745               Dessert Shop  
2298       35.666633       139.692420                Coffee Shop  
2299       35.669289       139.689620                     Bakery  

[2300 rows x 7 columns]

In [25]:
Tokyo_Ward_Venues['Venue Category'].value_counts()

Hotel                        161
Art Museum                   115
BBQ Joint                    115
Wagashi Place                 92
Garden                        92
Sake Bar                      92
Chinese Restaurant            69
Ramen Restaurant              69
History Museum                69
Japanese Restaurant           69
Japanese Curry Restaurant     69
Concert Hall                  69
Coffee Shop                   69
Park                          69
Yakitori Restaurant           46
Tonkatsu Restaurant           46
Soba Restaurant               46
Roof Deck                     46
Kaiseki Restaurant            46
Cocktail Bar                  46
Shrine                        46
Monument / Landmark           46
Bed & Breakfast               23
Vietnamese Restaurant         23
Art Gallery                   23
Seafood Restaurant            23
Udon Restaurant               23
Thai Restaurant               23
Café                          23
Botanical Garden              23
Nightclub 

In [26]:
tokyo_ward_venue_map = folium.Map(location=[latitude, longitude], zoom_start=12)

for lat, lng, label in zip(Tokyo_Ward_Venues['Venue Latitude'], Tokyo_Ward_Venues['Venue Longitude'], Tokyo_Ward_Venues['Venue Category']):
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        color='purple',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.5
    ).add_to(tokyo_ward_venue_map)
    
for lat, lng, neighborhood in zip(Tokyo_Ward_Venues['Latitude'], Tokyo_Ward_Venues['Longitude'], Tokyo_Ward_Venues['Special Ward']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html = True)
    folium.CircleMarker(
        [lat, lng],
        radius = 13,
        popup = label,
        color = 'Red',
        fill = True,
        fill_color = '#3186cc',
        fill_opacity = 0.7,
        parse_html = False).add_to(tokyo_ward_venue_map)
    
tokyo_ward_venue_map

## Based on the map, it looks like Shibuya, Shinjuku, Chiyoda, Chuo, Minato, and Taito could be ideal locations based on the amount of venues.